In [ ]:
using OrdinaryDiffEq
using PyPlot
using Printf
using Statistics

In [ ]:
using Random
Random.seed!(123)

In [ ]:
function kuramoto!(dthetadt, theta, p, t)
    n = length(theta)
    (K, omega) = p
    for i = 1:n
        si = 0.0
        ti = theta[i]
        for j = 1:n
            si += sin(theta[j] - ti)
        end
        dthetadt[i] = omega[i] + K/n * si
    end
end

In [ ]:
function phase_histogram(sol, t, np, omega0)
    th = reshape(sol(t), np)
    th = mod.(th .- omega0*t, 2*pi)
    # Histogram by Scott's normal reference rule
    stddev = std(th)
    scottbinwidth = 3.5*stddev/np^(1/3)
    scottnbins = Int(round(2*pi/scottbinwidth))
    hist(th, scottnbins, density=true, histtype="bar")
    ylim((0., 1.))
    xlim((0., 2*pi))
    titl = @sprintf("t = %6.3f", t)
    title(titl, font="monospace")
end


In [ ]:
(m, n) = (64, 64)
np = n*m
theta0 = 2*pi*rand(m, n);
omega0 = 3.0
omega = omega0 .+ randn(m, n);

In [ ]:
K_c = 2*sqrt(2/pi) # critical coupling parameter
a = 1.5 # 0.5
K = a * K_c

In [ ]:
tspan = (0.0, 25.0)
prob = ODEProblem(kuramoto!, theta0, tspan, (K, omega));
sol = solve(prob, Tsit5());

In [ ]:
lt = 520
ts = range(tspan[1], tspan[2], length=lt);

In [ ]:
fig1 = figure(1)
img = imshow(sin.(sol(0.)))
axis(false)
titl = @sprintf("t = %.3f", 0.0)
title(titl, font="monospace")

for t in ts[2:end]
    img.set_array(sin.(sol(t)))
    global titl = @sprintf("t = %6.3f", t)
    title(titl, font="monospace")
    display(fig1)
    sleep(0.1)
    IJulia.clear_output(true) 
end

In [ ]:
fig2 = figure(2)
phase_histogram(sol, ts[1], np, omega0)
for t in ts[2:end-1]
    phase_histogram(sol, t, np, omega0)
    display(fig2)
    sleep(0.1)
    IJulia.clear_output(true) 
    clf()
end
phase_histogram(sol, ts[end], np, omega0)


# Order parameter

In [ ]:
Ut = sol(ts);

In [ ]:
orderpar = similar(ts)
rr = similar(ts)
ii = similar(ts);

In [ ]:
for k = 1:lt
    s = 0.0
    for i = 1:n
        for j = 1:m
            s += exp(im*Ut.u[k][i, j])
        end
    end
    orderpar[k] = abs(s)/np
    rr[k] = real(s)/np
    ii[k] = imag(s)/np
end

In [ ]:
figure(3)
plot(rr, ii)
grid(true)
axis("square")
xlabel(L"Re")
ylabel(L"Im")
title("Order parameter: phase space trajectory")

In [ ]:
figure(4)
plot(ts, orderpar)
grid(true)
xlabel(L"t")
ylabel(L"$\|r(t)\|$")
title("Order parameter")

In [ ]:
# time derivatives
redot = similar(rr)
imdot = similar(ii)
dt = ts[2] - ts[1]
redot[1] = (rr[2] - rr[1])/dt
imdot[1] = (ii[2] - ii[1])/dt
for i = 2:lt-1
    redot[i] = (rr[i+1] - rr[i-1])/(2*dt)
    imdot[i] = (ii[i+1] - ii[i-1])/(2*dt)
end
redot[lt] = (rr[lt] - rr[lt-1])/dt
imdot[lt] = (ii[lt] - ii[lt-1])/dt;

In [ ]:
freq = similar(orderpar)
freq .= (rr .* imdot - ii .* redot) ./ (orderpar.^2);

In [ ]:
figure(5)
plot(ts, freq)
grid(true)
xlabel(L"t")
ylabel(L"\omega(t)")
ylim(0., 6.0)
title("Frequiency")